In [14]:
import nltk, re, pprint
from nltk.stem import PorterStemmer
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.corpus import stopwords

import pandas as pd
import numpy as np

import sys
import pymysql

ps = PorterStemmer()

In [419]:
def cleaning_ing_list(ingredients):
        
        #getting a list of stop phrases
        stop_phrases = [stop_words.rstrip('\n') for stop_words in open("recipe_stopwords.txt")]
        final_list = []
        
        for ing in ingredients:
            
            #removing text in brackets
            ing = re.sub("\s?[\(\[].*?[\)\]]", "", ing)
            
            #removing anything extra in the ingredient discription (after ',')
            if "," in ing:
                clean_ing , extra = ing.split(',', 1)
                ing = clean_ing
            
            #getting ing discription words
            ing_words = ing.split()

            #getting all amount values
            i = 0
            amounts = []
            for w in ing_words:
                
                #if first char in line is a digit
                if w[0].isdigit(): 
                    amounts.append(ing_words[i])
                    i+=1
                    
            #removing the amount values of the ingredient
            if amounts:
                for a in amounts:
                    ing_words.remove(a)

            #removing stopwords
            filtered_ing = [w for w in ing_words if w not in stop_phrases]
            
            #stemming
            clean_ing = []
            for word in filtered_ing:
                clean_ing.append(ps.stem(word))
            
            #lower caseing & appending
            final_list.append(' '.join(clean_ing).lower())
            
        return final_list

In [407]:
def clean_time(string):
    
    h_match = re.findall(r"([0-9]+\s?[h]+)", string, re.I)
    m_match = re.findall(r"([0-9]+\s?[m]+)", string, re.I)
    to_match = re.findall(r"([0-9]+\s[t][o]\s+[0-9])", string, re.I) #eg. "1 to 2 hours"
    
    hours = 0
    minutes = 0
    
    #key phrase search
    if "to" in string:
        if to_match:
            string = string.split("to")[1]
            
        else:
            string = string.split("to")[0]

    #if contains hours
    if h_match:
        hours = int(re.findall(r'\d+', str(h_match))[0])
            
    #if contains min
    if m_match:
        minutes = int(re.findall(r'\d+', str(m_match))[0])
        
    #if does not contains min or hours
    if not h_match and not m_match:
        
        if "overnight" in string:
            hours = 8
            
        else:
            print("time input error: ", string)
        
    else:
        return hours*60 + minutes

In [441]:
f = open('content.txt', 'r', encoding = "utf-8")

line_num = 1
ing_num = 0
ingredients = []
description = ""

for line in f.readlines():
    
    if line_num == 1:
        url = line
        print("URL: " , url)
        line_num += 1
        continue
    
    if line_num == 2:
        img_url = line
        print("image URL: " , img_url)
        line_num += 1
        continue
        
    if line_num == 3:
        title = line
        print("recipe title: " , title)
        line_num += 1
        continue
        
    if line_num == 4:
        
        if "preptime" in line:
            
            #printing discription in a single line
            print("discription: " , re.sub("\n", "", description))
            line_num += 1
            continue
        
        else:
            description = description + " " + line
            continue
        
    if line_num == 5:
        prep_time = clean_time(line)
        print("\nprep time: ", prep_time , " min.\n")
        line_num += 1
        continue
        
    if line_num == 6:
        cook_time = clean_time(line)
        print("cook time: ", cook_time , " min.\n")
        line_num += 1
        continue
        
    if line_num == 7:
        
        try:
            servings = int(re.findall(r'\d+',line)[0])
        except:
            servings = 1 #e.g. "Makes one jar"
            
        print("servings: ", servings, "\n")
        line_num += 1
        continue
        
    if "*****eol*****" in line:
        
        clean_ingredients = cleaning_ing_list(ingredients)
        
        print("ingredients: ", clean_ingredients)
        print("\nnum of ingredients: ", ing_num)
        print("-----")
        
        line_num = 1
        ing_num = 0
        ingredients = []
        description = ""
        
        continue
        
    if line_num > 7:
        
        print(line)

        #words of an ingridient entry
        line_words = line.split()

        #key words search
        if "and" in line_words:
            primary_ing, extra_ing = line.split("and", 1)
            ingredients.extend([primary_ing, extra_ing])
            ing_num += 1 #count extra ing
            
        elif "plus extra" in line:
            primary_ing, extra_same = line.split("plus extra", 1)
            ingredients.append(primary_ing) 
            #excluding since the same ingridient is used

        elif "plus" in line_words:
            primary_ing, extra_ing = line.split("plus", 1)
            ingredients.extend([primary_ing, extra_ing])
            ing_num += 1 #count extra ing
        
        #dure to the similarity in spelling for and or are special case
        elif "or" in line_words:
            
            #looking at the possitions of word in line
            if "for" in line_words:
                pos_for = line.find("for")
                pos_or = line.find("or", 1)
                
                if pos_for > pos_or:
                    primary_ing, alternative = line.split("or", 1)
                    alt_ing, why_needed  = alternative.split("for", 1)
                    ingredients.extend([primary_ing, alt_ing])
                    #not counting alternative ingridient
            
                else:
                    primary_ing, why_needed  = line.split("for", 1)
                    ingredients.append(primary_ing) 
                    #excluding why ingredient is needed
                
            else:
                primary_ing, alt_ing = line.split("or", 1)
                ingredients.extend([primary_ing, alt_ing])
                #not counting alternative ingridient

        else:
            ingredients.append(line)
        
        ing_num += 1
        line_num += 1
        continue

    else:
        print("error")
              
f.close()

URL:  https://www.bbc.co.uk/food/recipes/pastawithpurplesprou_3417

image URL:  https://ichef.bbci.co.uk/food/ic/food_16x9_832/recipes/pastawithpurplesprou_3417_16x9.jpg

recipe title:  Pasta with purple sprouting broccoli

discription:   Purple sprouting broccoli can be a cheap and cheerful ingredient for early spring dinners and goes brilliantly with anchovy and chilli.

prep time:  30  min.

cook time:  30  min.

servings:  4 

1kg/2¼lb purple sprouting broccoli

1 medium sized fresh red chilli (not too hot)

2 cloves garlic, peeled

1 small tin of anchovy fillets in olive oil, drained

good quality olive oil

350g/12oz pasta fusilli, oriecchiette, penne rigate or conchiglie are the most suitable shapes

4 tbsp freshly grated parmesan or hard pecorino cheese

salt and pepper

ingredients:  ['purpl sprout broccoli', 'medium size fresh red chilli', 'clove garlic', 'small tin of anchovi fillet in oliv oil', 'good qualiti oliv oil', 'pasta fusilli', 'iecchiett', 'tbsp freshli grate parm


100g/3½oz caster sugar

2 cinnamon sticks

5 star anise

3 tbsp lemon juice

1 pomelo (approximately 900g/2lb)

600g/1lb 5oz Brussels sprouts, trimmed

250g/9oz shallots

5 tbsp olive oil

2 tbsp chopped coriander leaves

salt and freshly ground black pepper

ingredients:  ['medium butternut squash', 'cut into small cube', 'tbsp oliv oil', 'best-qual shortcrust pastri', 'plain flour', 'stilton', 'membrillo', 'free-rang egg', 'oz doubl cream', 'oz crème fraîch', 'salt', 'freshli ground black pepper', 'caster sugar', 'cinnamon stick', 'star anis', 'tbsp lemon juic', 'pomelo', 'brussel sprout', 'shallot', 'tbsp oliv oil', 'tbsp chop coriand leav', 'salt', 'freshli ground black pepper']

num of ingredients:  23
-----
URL:  https://www.bbc.co.uk/food/recipes/chocolate_roulade_79152

image URL:  https://ichef.bbci.co.uk/food/ic/food_16x9_832/recipes/chocolate_roulade_79152_16x9.jpg

recipe title:  Chocolate roulade 

discription:   Mary Berry's gorgeous chocolate roulade is made without flo

ingredients:  ['tsp veget oil', 'pancetta', 'larg onion', 'carrot', 'fine chop', 'celeri stick', 'fine chop', 'garlic clove', 'tbsp thyme leav', 'bay leaf', 'litres/2¾ pint chicken stock', 'tin chop tomato', 'red lentil', 'chines leaf cabbag', 'savoy cabbag', 'larg hand fresh flatleaf parsley', 'sea salt', 'freshli ground black pepper']

num of ingredients:  17
-----
URL:  https://www.bbc.co.uk/food/recipes/bilberry_tart_tarteaux_08943

image URL:  https://ichef.bbci.co.uk/food/ic/food_16x9_832/recipes/bilberry_tart_tarteaux_08943_16x9.jpg

recipe title:  Blueberry tart (Tarte aux myrtilles)

discription:   Rick Stein's blueberry tart recipe, with ground almonds and egg custard is the perfect mix of comforting and refined. The tart is really stuffed with fruit with a very light binding of egg custard.

prep time:  120  min.

cook time:  90  min.

servings:  8 

210g/7¼oz plain flour, plus extra for dusting

pinch salt

100g/3½oz butter, chilled and diced

40g/1½oz caster sugar

1 free-

ingredients:  ['plain chocol', 'caster sugar', 'oz boil water', 'salt butter', 'free-rang egg', 'tsp instant coffe powder', 'tsp vanilla extract', 'oz crème fraîch', 'summer berri', 'tbsp plain chocol', 'ice sugar']

num of ingredients:  11
-----
URL:  https://www.bbc.co.uk/food/recipes/punjabi_chicken_curry_44800

image URL:  https://ichef.bbci.co.uk/food/ic/food_16x9_832/recipes/punjabi_chicken_curry_44800_16x9.jpg

recipe title:  Punjabi chicken curry 

discription:   This super-easy, hearty chicken curry layers up earthy spices, including cardamom and turmeric with zingy root ginger and fresh coriander leaves. 

prep time:  30  min.

cook time:  90  min.

servings:  4 

4 tbsp vegetable oil

1½ tsp cumin seeds, ground in a pestle and mortar

5cm/2in cinnamon stick

8 green cardamom pods

300g/10½oz onions, thinly sliced

7 garlic cloves, finely chopped

5cm/2in fresh root ginger, peeled and finely chopped

1½ tsp ground turmeric 

1 tsp mild chilli powder

350g/12oz tomatoes, blend

ingredients:  ['brussel sprout', 'halv', 'bake potato', 'in 2-3cm dice', 'wholewheat t', 'tiglioni or penn', 'salt', 'ricotta', 'gruyèr', 'unsalt butter', 'tbsp garlic oil', 'sage leav', 'parmesan']

num of ingredients:  12
-----
URL:  https://www.bbc.co.uk/food/recipes/masala_omelette_with_80543

image URL:  https://ichef.bbci.co.uk/food/ic/food_16x9_832/recipes/masala_omelette_with_80543_16x9.jpg

recipe title:  Masala omelette with parathas

discription:   A spicy masala omelette is my ‘go to’ weekend brunch. My mother always made it for us in India. The combination of ground spices, chillies and eggs just works. It's lightly crisp around the edges but moist, with a fiery chilli kick. It's great served with parathas. 

prep time:  30  min.

cook time:  30  min.

servings:  2 

½ tsp cumin seeds

1 tsp coriander seeds

2 green chillies

1 large onion, finely chopped (200g)

2 tbsp fresh coriander, roughly chopped

½ tsp kashmiri chilli powder (or mild paprika)

½ tsp ground turmeric 

...

ingredients:  ['pork belli', 'tbsp groundnut oil', 'tsp sugar', '7fl oz chicken stock', 'whole star anis', 'stick cinnamon', 'cassia bark', 'piec fresh ginger', 'tbsp shaox wine', 'oz dark soy sauc', 'pinch freshli ground black pepper', 'spring onion']

num of ingredients:  11
-----
URL:  https://www.bbc.co.uk/food/recipes/raspberry_and_pistachio_61368

image URL:  https://ichef.bbci.co.uk/food/ic/food_16x9_832/recipes/raspberry_and_pistachio_61368_16x9.jpg

recipe title:  Raspberry and pistachio éclairs

discription:   If you aren't up to the challenge of  Paul's choux pastry tower,  you can still enjoy the same gorgeous flavours in these easier éclairs.

prep time:  90  min.

cook time:  90  min.

servings:  24 

100g/3½oz unsalted butter, cut into roughly 1cm/½in cubes

pinch of salt

130g/4½oz very strong white bread flour

2 large free-range eggs, beaten

400ml/14fl oz full-fat milk

2 tbsp pistachio paste

100g/3½oz caster sugar

4 large free-range egg yolks

40g/1½oz cornflour



ingredients:  ['½ tbsp light oliv oil', 'larg onion', 'garlic clove', 'beef stock cube', 'tsp sweet smoke paprika', 'tbsp tomato puré', 'tin beef consommé', 'chestnut mushroom', 'tbsp dijon mustard', 'rump steak', 'oliv oil spray', 'c', 'nichon or small gherkin', 'oz half-fat crème fraîch', 'tbsp fine chop flatleaf parsley', 'tbsp roughli chop chervil', 'parsley', 'tbsp dri onion flake', 'sea salt', 'freshli ground black pepper', 'basmati rice']

num of ingredients:  19
-----
URL:  https://www.bbc.co.uk/food/recipes/seashell_caramels_89965

image URL:  https://ichef.bbci.co.uk/food/ic/food_16x9_832/recipes/seashell_caramels_89965_16x9.jpg

recipe title:  Seashell caramels

discription:   These pretty dark chocolate shells are filled with caramel and sealed with a white chocolate base.   Equipment: You will need 20 assorted seashell or similar chocolate moulds and a sugar thermometer.

prep time:  30  min.

cook time:  90  min.

servings:  20 

300g/10½oz dark chocolate (use a good bar 

ingredients:  ['medium onion', 'clove of garlic', 'a thick slice of butter', 'a thumb-siz piec of ginger', 'green cardamom pod', 'a tsp ground cumin', '½ tsp ground turmer', 'a coupl of pinch of ground cinnamon', 'a cinnamon stick', 'a good pinch of ground chilli', 'bay leav', 'assort mushroom', 'spinach', 'hand skin hazelnut', 'a gener hand of raisin', 'golden sultana', 'plain yoghurt', 'crème fraîch', 'rice', 'bread']

num of ingredients:  18
-----
URL:  https://www.bbc.co.uk/food/recipes/chicory_gratin_84963

image URL:  https://ichef.bbci.co.uk/food/ic/food_16x9_832/recipes/chicory_gratin_84963_16x9.jpg

recipe title:  Chicory gratin

discription:   A beloved classic of Belgian cooking; this is a simple, rustic family dish. The Comté cheese can be replaced by any British cheese. And, of course, omit the ham for a vegetarian version.

prep time:  30  min.

cook time:  120  min.

servings:  2 

4 heads yellow chicory

1 tbsp lemon juice

1 tbsp sugar

2 large pinches sea salt

6 whit

ingredients:  ['tbsp oil', 'beef minc', 'onion', 'stick celeri', 'plain flour', 'oz red wine', 'pint beef stock', 'tbsp worcestershir sauc', 'tbsp light muscovado sugar', 'tbsp chop thyme', 'small brown chestnut mushroom', 'dash of gravi brown', 'salt', 'pepper', 'king edward potato', 'into 4mm slice', 'oz doubl cream', 'strong cheddar']

num of ingredients:  18
-----
URL:  https://www.bbc.co.uk/food/recipes/rick_steins_tiramisu_18785

image URL:  https://ichef.bbci.co.uk/food/ic/food_16x9_832/recipes/rick_steins_tiramisu_18785_16x9.jpg

recipe title:  Rick Stein's tiramisu

discription:   Why, you may ask, do we need another recipe for tiramisu? It is now as common as apple crumble. But I was particularly taken by this one in Venice, which had elevated the pudding to a fine-dining level simply by putting it in a cocktail glass and using a whisked fatless sponge.

prep time:  None  min.

cook time:  30  min.

servings:  4 

3 eggs, separated

75g/2¾oz caster sugar

75g/2¾oz plain flour

ingredients:  ['tsp sesam oil', 'banana shallot', 'fine slice', 'garlic clove', 'sprig thyme', 'dri mushroom', 'flat mushroom', 'pinch sea salt', 'pinch freshli ground white pepper', 'tsp soy sauc', 'tsp sesam oil', 'carrot', 'fine chop ginger', 'chilli', 'chop', 'oyster mushroom', 'beansprout', 'pinch salt', 'pinch black pepper', 'chines lettuc', 'coriand leav', 'spring onion', 'a squeez of lemon juic']

num of ingredients:  23
-----
URL:  https://www.bbc.co.uk/food/recipes/pork_and_apple_burger_94249

image URL:  https://ichef.bbci.co.uk/food/ic/food_16x9_832/recipes/pork_and_apple_burger_94249_16x9.jpg

recipe title:  Pork and apple burgers

discription:   This pork burger recipe from Eat Well for Less makes enough for two meals so you can pop half in the freezer for a quick dinner. Try it as meatballs, too.  Each burger serving provides 300 kcal, 23g protein, 25g carbohydrates (of which 5g sugars), 12g fat (of which 4g saturates), 2g fibre and 0.5g salt.    Each serving provides 37